In [1]:
import os
from glob import glob
import pathlib
import shutil

import earthpy as et
import earthpy.earthexplorer as etee
import earthpy.spatial as es
import geopandas as gpd
import geoviews as gv
import holoviews as hv
import hvplot.pandas
import hvplot.xarray
import numpy as np
import pandas as pd
import panel as pn
import rioxarray as rxr
import rioxarray.merge as rxrm

data_dir = os.path.join(et.io.HOME, et.io.DATA_NAME)
oak_dir = os.path.join(data_dir, 'oakland-neighborhoods')
ndvi_dir = os.path.join(data_dir, 'oakland-green-space', 'processed')

for a_dir in [data_dir, oak_dir, ndvi_dir]:
    if not os.path.exists(a_dir):
        os.makedirs(a_dir)

In [2]:
# Download neighborhoods shapefile and create GDF of Oakland
oak_path = os.path.join(data_dir, 'earthpy-downloads', 'CEDA_Nhhods02', 'CEDA_Nhhods02', 'CEDA_Neighborhoods2002.shp')
if not os.path.exists(oak_path):
    oak_url = ('http://data.openoakland.org/sites/default/files/'
               'CEDA_Nhhods02.zip')
    oak_zip = et.data.get_data(url=oak_url)

oak_gdf = gpd.read_file(oak_path).set_index('NAME').to_crs(4326)
neigh_gdf = (
    oak_gdf.
    loc[['Montclair']]
)
oak_gdf

geometry
NAME                                                              
Montclair        POLYGON ((-122.21595 37.83218, -122.19901 37.8...
Shepherd Canyon  POLYGON ((-122.20487 37.83064, -122.18881 37.8...
Not Named6       POLYGON ((-122.23066 37.84902, -122.22917 37.8...
Glen Highlands   POLYGON ((-122.22824 37.84579, -122.22517 37.8...
Golden Gate      POLYGON ((-122.28252 37.83801, -122.28238 37.8...
...                                                            ...
Waverly          POLYGON ((-122.26126 37.81146, -122.26096 37.8...
Webster          POLYGON ((-122.16595 37.75329, -122.16635 37.7...
Woodland         POLYGON ((-122.17760 37.75361, -122.17735 37.7...
Woodminster      POLYGON ((-122.17843 37.80374, -122.18510 37.7...
Upper Dimond     POLYGON ((-122.20013 37.79744, -122.20053 37.7...

[133 rows x 1 columns]

In [3]:
def download_neighborhood_data(name, geometry, start, end):
    """
    Download NAIP raster for a given geometry, start date, and end date

    Parameters
    ==========
    name : str
      The name used to label the download
    geometry : shapely.POLYGON
      The geometry to derive the download extent from. 
      Must have a `.bounds` attribute.
    start : str
      The start date as 'YYYY-MM-DD'
    end : strL
      The end date as 'YYYY-MM-DD'

    Returns
    =======
    downloader : earthpy.earthexplorer.EarthExplorerDownloader
      Object with information about the download, including the data directory.
    """
    
    print(f'Downloading NAIP for {name}')
    bbox = etee.BBox(*geometry.bounds)
    print(geometry.bounds)
    #label = row.pri_neigh.lower().replace(' ', '-')
    naip_downloader = etee.EarthExplorerDownloader(
        dataset="NAIP", 
        label=name.lower().replace(' ', '-'), 
        bbox=bbox,
        start=start, 
        end=end,
        store_credential=True)
    #print(naip_downloader.label)
    #print(naip_downloader.bbox.urx, naip_downloader.bbox.ury)
    naip_downloader.submit_download_request()
    #naip_downloader.wait_for_available_downloads()
    naip_downloader.download(override=True)
    return naip_downloader

In [4]:
def load_and_merge_arrays(name):
    """
    Load in and merge downloaded arrays
    
    Parameters
    ==========
    name : str
      The name used to label the download

    Returns
    =======
    merge_da : rxr. DataArray
        DataArray with the merged data
    """
    
    print(f'Merging array for {name}')
    data_path = os.path.join(
        et.io.HOME, et.io.DATA_NAME,
        name.lower().replace(' ', '-'))
    tif_paths = glob(os.path.join(data_path, '*.tif'))
    das = [rxr.open_rasterio(tp, masked=True) for tp in tif_paths]
    merged_da = rxrm.merge_arrays(das)
    return merged_da

In [5]:
def calculate_ndvi_statistics(gdf, da, stats_path, override=False):
    """
    Calculate NDVI, then summarize and save statistics
    
    Uses downloaded National Agricultural Imagery Program (NAIP)
    data.
    
    Parameters
    ==========
    gdf : gpd.GeoDataFrame
      A geodataframe with a single row/neighborhood name/boundary
    da : rxr.DataArray
      Multispectral (NAIP) raster data
    stats_path : pathlike
      Path to the statistics CSV file
    """
    name = str(gdf.index[0])
    print(f'Calculate NDVI and statistics for {name}')
    # Caching for existing data
    file_is_empty = True
    if os.path.exists(stats_path):
        print('Stats file exists.')
        stats_df = pd.read_csv(stats_path)
        file_is_empty = len(stats_df)==0
        print(f'Stats file is empty? {file_is_empty}')
        
        if not file_is_empty:
            if (name in list(stats_df.neighborhood)) and (not override):
                print(f'Stats exist for {name}, skipping')
                return            
            
    reprojected_gdf = gdf.to_crs(da.rio.crs)
    # clip the NAIP tile to the bounds of the neighborhood gdf
    naip_crop_da = da.rio.clip_box(*reprojected_gdf.total_bounds)

    # Clip to extent of neighborhood
    naip_da = naip_crop_da.rio.clip(reprojected_gdf.geometry)

    # Calculate NDVI
    ndvi_da = (
        (naip_da.sel(band=4) - naip_da.sel(band=1))
        / (naip_da.sel(band=4) + naip_da.sel(band=1))
    )

    #Calculate NDVI stats for neighborhood and append to CSV
    print(f'Writing stats for {name}')
    mode = 'w' if file_is_empty else 'a'
    pd.DataFrame(dict(
        neighborhood=[name],
        ndvi_minimum=[float(ndvi_da.min())],
        ndvi_maximum=[float(ndvi_da.max())],
        ndvi_median=[float(ndvi_da.median())],
        ndvi_25pctl=[np.nanpercentile(ndvi_da.values, 25)],
        ndvi_75pctl=[np.nanpercentile(ndvi_da.values, 75)],
        ndvi_mean=[float(ndvi_da.mean())],
        ndvi_stddev=[float(ndvi_da.std())]
        )).to_csv(stats_path, mode='a', header=file_is_empty, index=False)

In [6]:
ndvi_stats_path = os.path.join(ndvi_dir, 'oakland_neighborhood-ndvi-stats.csv')

for neighborhood_name, details in oak_gdf.iterrows():
    if not os.path.exists(ndvi_stats_path):
        print('NDVI stats file does not exist...')
        ndvi_stats_df = pd.DataFrame()
    else:
        ndvi_stats_df = pd.read_csv(ndvi_stats_path, index_col="neighborhood")
    if neighborhood_name in ndvi_stats_df.index:
        print(f'Neighborhood stats for {neighborhood_name} have already been calculated. Skipping')
        continue
    
    try:
        downloader = download_neighborhood_data(
            neighborhood_name, details.geometry, '2021-01-01', '2021-12-31')
    
    except (ValueError, TypeError):
        print('Download not available. Try different date range.')
        try:
            downloader = download_neighborhood_data(
                neighborhood_name, details.geometry, '2022-01-01', '2022-12-31')
        except (ValueError, TypeError):
            print('Data cannot be found. Skipping neighborhood.')
            continue
    # downloader = download_neighborhood_data(
    #     neighborhood_name, details.geometry, '2022-01-01', '2022-12-31')
    merged_da = load_and_merge_arrays(neighborhood_name)
    calculate_ndvi_statistics(oak_gdf.loc[[neighborhood_name]], merged_da, ndvi_stats_path)
    del merged_da
    
    # shutil.rmtree(downloader.data_dir)

Neighborhood stats for Montclair have already been calculated. Skipping
Neighborhood stats for Shepherd Canyon have already been calculated. Skipping
(-122.23066288319785, 37.845140768917474, -122.20982320460696, 37.86375221520572)
Login Successful.
Searching datasets...
Using dataset alias: naip
Searching scenes...
Found 0 scenes
Download not available. Try different date range.
(-122.23066288319785, 37.845140768917474, -122.20982320460696, 37.86375221520572)
Login Successful.
Searching datasets...
Using dataset alias: naip
Searching scenes...
Found 1 scenes
1 products found.
Downloads staging...
Data cannot be found. Skipping neighborhood.
(-122.22824182380305, 37.832882050236535, -122.21529841589657, 37.84704066614924)
Login Successful.
Searching datasets...
Using dataset alias: naip
Searching scenes...
Found 0 scenes
Download not available. Try different date range.
(-122.22824182380305, 37.832882050236535, -122.21529841589657, 37.84704066614924)
Login Successful.
Searching dataset

In [20]:
ndvi_stats_df = pd.read_csv(ndvi_stats_path, index_col="neighborhood")
chloropleth = gv.tile_sources.EsriNatGeo*gv.Polygons(
    oak_gdf.join(ndvi_stats_df, how='left'),
    vdims=['ndvi_mean']
).options(
    width=800,
    height=600,
    title="NDVI Values for Oakland Neighborhoods"
)
hv.save(chloropleth, 'oakland_chloropleth.html')
chloropleth

:Overlay
   .WMTS.I     :WMTS   [Longitude,Latitude]
   .Polygons.I :Polygons   [Longitude,Latitude]   (ndvi_mean)